In [1]:
from glob import glob

import os

[ os.path.basename(f) for f in glob('../../llama/raw/delta/**/*')]

['Einstein-v6.1-Llama3-8B',
 'L3-TheSpice-8b-v0.8.3',
 'dolphin-2.9-llama3-8b',
 'Configurable-Hermes-2-Pro-Llama-3-8B',
 'MAmmoTH2-8B-Plus',
 'badger',
 'Pantheon-RP-1.0-8b-Llama-3',
 'Tiamat-8b-1.2-Llama-3-DPO',
 'Buzz-8b-Large-v0.5',
 'Kei_Llama3_8B',
 'Llama-3-Lumimaid-8B-v0.1',
 'llama-3-cat-8b-instruct-pytorch',
 'Llama-3SOME-8B-v1',
 'Roleplay-Llama-3-8B',
 'Llama-3-LewdPlay-8B-evo',
 'meta-llama-3-8b-instruct-hf-ortho-baukit-5fail-3000total-bf16',
 'Llama-3-8B-Instruct-Coder',
 'opus-v1.2-llama-3-8b-instruct-run3.5-epoch2.5',
 'Poppy_Porpoise-0.72-L3-8B',
 'Llama-3-8B-Instruct-norefusal',
 'Meta-Llama-3-8B-Instruct-DPO',
 'meta-llama-3-8b-instruct-hf-ortho-baukit-34fail-3000total-bf16',
 'llama-3-lumimaid-habib-v7',
 'Llama-3-Refueled',
 'Llama-3-8B-Instruct-DPO-v0.4',
 'Llama-3-8B-Instruct-Gradient-1048k',
 'Mahou-1.0-llama3-8B',
 'Llama-3-SauerkrautLM-8b-Instruct',
 'Llama-3-Soliloquy-8B-v2']

In [2]:
import sys
sys.path.append("../mergekit")

In [3]:
from ztrain.io import list_for_path

models = [
 'Einstein-v6.1-Llama3-8B',
 'L3-TheSpice-8b-v0.8.3',
 'dolphin-2.9-llama3-8b',
 'Configurable-Hermes-2-Pro-Llama-3-8B',
 'MAmmoTH2-8B-Plus',
 'Pantheon-RP-1.0-8b-Llama-3',
 'Tiamat-8b-1.2-Llama-3-DPO',
 'Buzz-8b-Large-v0.5',
 'Kei_Llama3_8B',
 'Llama-3-Lumimaid-8B-v0.1',
 'llama-3-cat-8b-instruct-pytorch',
 'Llama-3SOME-8B-v1',
 'Roleplay-Llama-3-8B',
 'Llama-3-LewdPlay-8B-evo',
 #'Llama-3-8B-Instruct-Coder',
 'opus-v1.2-llama-3-8b-instruct-run3.5-epoch2.5',
 'meta-llama-3-8b-instruct-hf-ortho-baukit-5fail-3000total-bf16',
 'Poppy_Porpoise-0.72-L3-8B',
 'Llama-3-8B-Instruct-norefusal',
 'Meta-Llama-3-8B-Instruct-DPO',
 'badger',
 #'llama-3-lumimaid-habib-v7',
 'Llama-3-Refueled',
 'Llama-3-8B-Instruct-DPO-v0.4',
 'Llama-3-8B-Instruct-Gradient-1048k',
 'Mahou-1.0-llama3-8B',
 'Llama-3-SauerkrautLM-8b-Instruct',
 'Llama-3-Soliloquy-8B-v2'
]

out_model = "opus-v1.2-llama-3-8b-instruct-run3.5-epoch2.5"
in_model = "Llama-3-8B-Instruct-Gradient-1048k"
model_names, subtypes, model_list, group_idx = list_for_path(path="../../llama/raw/delta/", include_folders=models, search="/**/*")

In [4]:
from mergekit.io import ShardedTensorIndex, TensorWriter, LazyTensorLoader
import os
import torch
from transformers import AutoModelForCausalLM, AutoTokenizer
from typing import Dict, Tuple, Optional
from ztrain.stats import gen_stats
from ztrain.model import get_layer_type
from ztrain.tensors import merge_tensors_fft2_autoscale, correlate_pairs, least_correlated_pairs
from ztrain.util import get_device, cuda_memory_profiler

shards = [ShardedTensorIndex.from_disk(model_list[ix]) for model, ix in group_idx.items()]
instruct_shard = ShardedTensorIndex.from_disk(os.path.join("../../llama/raw/base", "Meta-Llama-3-8B-Instruct-hf"))
device = get_device()

model_o_path = os.path.join("../../llama/raw/base", "Meta-Llama-3-8B-hf")
trust_remote_code = True
config = {
    'torch_dtype': torch.bfloat16,
    'low_cpu_mem_usage': True,
    'trust_remote_code': trust_remote_code,
}

set_mask = {}

embedding_size = 128256

base_model = AutoModelForCausalLM.from_pretrained(model_o_path, **config).to("cpu")
base_model.resize_token_embeddings(embedding_size)
result_dict : dict[str, torch.Tensor] = base_model.state_dict()
keys = list(result_dict.keys())
mc = len(model_list)
layers = len(keys)

out_folder = "./maldv/badger-augment"

writer = TensorWriter(out_folder)

print(f"Loaded Base Model {base_model.name_or_path} with {len(keys)} keys and dtype {result_dict[keys[0]].dtype}")

kid = 0


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

Loaded Base Model ../../llama/raw/base/Meta-Llama-3-8B-hf with 291 keys and dtype torch.bfloat16


In [6]:
kid = 0
sk = 1
ek = -(2)# + 9 + 9 + 9)
primary = "cuda:0"
secondary = "cuda:1"
cold = "cpu"
work_device = primary
alternate_device = secondary
for j, k in enumerate(keys[kid:], start=kid):
    m0 : torch.Tensor = result_dict[k].to(work_device).to(torch.float32)
    tensor_size = m0.numel() * 4
    print(f"Tensor Size {tensor_size} {m0.shape}")
    norm, cosine, minv, maxv = gen_stats(m0, None)
    m = in_model if (j / len(keys)) < .5 else out_model
    mix = model_names.index(m)
    mx : torch.Tensor = LazyTensorLoader(shards[mix]).get_tensor(k, work_device).to(torch.float32)
    norm, cosine, minv, maxv = gen_stats(mx, None)
    mx_norm = torch.norm(m0.to(torch.float32)).item()
    mx = mx.to(cold)
    print(f"Base Model {j} {k} {norm} {minv} {maxv} {m0.shape}")
    if k in keys[:sk]:
        print(f"Copying {k} {m} {m0.shape}")
        writer.save_tensor(k, mx.to(torch.bfloat16), clone=True)
        del mx, m0
    elif k in keys[ek:]:
        print(f"Copying {k} {m} {m0.shape}")
        writer.save_tensor(k, mx.to(torch.bfloat16), clone=True)
        del mx, m0
    else: 
        del mx
        with cuda_memory_profiler():
            block, layer, layer_type, layer_name = get_layer_type(k)
            layer_stack : list[tuple[str, torch.Tensor]]= []
            mean_norms : list[torch.float32] = []
            mi = LazyTensorLoader(instruct_shard).get_tensor(k, work_device).to(torch.float32) - m0
            for i, m in enumerate(model_names):
                mix = model_names.index(m)
                subtype = subtypes[mix]
                m1 : Optional[torch.Tensor] = LazyTensorLoader(shards[mix]).get_tensor(k, work_device).to(torch.float32)
                if j == 0 or j == layers - 1:
                    if m1.shape[0] > embedding_size:
                        # we need to resize the embeddings
                        print(f"Resizing embeddings from {m1.shape[0]} to {embedding_size}.  If this is in an input layer, it may be catastrophic")
                        m1 = m1[:embedding_size]
                    if m1.shape[0] < embedding_size:
                        print(f"Padding embeddings from {m1.shape[0]} to {embedding_size}.  If this is in an input layer, it may be catastrophic")
                        m1 = torch.cat([m1, torch.zeros(embedding_size - m1.shape[0], m1.shape[1])], dim=0)
                elif m1.shape != m0.shape:
                    print(f"ismatch {m} for {k} {m1.shape} {m0.shape}")
                    continue
                if subtype == 'base':
                    m1 = m1 + mi
                
                m1 = m1 - m0
                m1_norm = torch.norm(m1.to(torch.float32)).item()
                mean_norms.append(m1_norm)
                layer_stack.append([f"{m}-{i}", m1.to(cold)])
                del m1
            m0 = m0.to(cold)
            del mi

            mean_norm = torch.tensor(mean_norms).median().item()
            del mean_norms
            
            correlation = correlate_pairs(torch.stack([s[1] for s in layer_stack], dim=0))
            while len(layer_stack) > 1:
                next_stack = []
                for x, y, corr in least_correlated_pairs(correlation):
                    if y >= 0:
                        a = layer_stack[x][1].to(primary)
                        b = layer_stack[y][1].to(primary)
                        a_key = layer_stack[x][0]
                        b_key = layer_stack[y][0]
                        if len(a_key) < len(b_key):
                            a, b = b, a
                            a_key, b_key = b_key, a_key
                        remaining_keys = [i[0] for i in layer_stack if i[0] not in [a_key, b_key]]

                        merge, norm_a, norm_b = merge_tensors_fft2_autoscale(a, b, .5)
                        merge = merge * mean_norm
                        post_norm = torch.norm(merge.to(torch.float32))
                        print(f"Pair {mean_norm:.3f} {post_norm:.3f} {corr:.7f} [ratio: {norm_a:.3f} {norm_b:.3f}] {merge.sum():.3f} ] {a_key} :: {b_key}") # [left: {', '.join(remaining_keys)}]")
                        del a, b, post_norm
                        next_stack.append([f"{a_key}_{b_key}", merge.to(cold).detach()])
                    else:
                        next_stack.append(layer_stack[x])
                        print(f"Skipping {layer_stack[x][0]}")

                del layer_stack
                layer_stack = next_stack
                correlation = correlate_pairs(torch.stack([s[1] for s in layer_stack], dim=0))

            result = layer_stack[0][1]
            writer.save_tensor(k, (m0.to(work_device) + result.to(work_device)).to(torch.bfloat16), clone=True)
            print(f"Saving {k} {result.shape} {result.dtype}")
            del result, m0, mean_norm
    if j % 30 == 0:
        writer.flush_current_shard()

writer.finalize()

Tensor Size 2101346304 torch.Size([128256, 4096])
Base Model 0 model.embed_tokens.weight 213.1804962158203 -0.0810546875 0.224609375 torch.Size([128256, 4096])
Copying model.embed_tokens.weight Llama-3-8B-Instruct-Gradient-1048k torch.Size([128256, 4096])
Tensor Size 67108864 torch.Size([4096, 4096])
Base Model 1 model.layers.0.self_attn.q_proj.weight 72.73050689697266 -0.7734375 0.6875 torch.Size([4096, 4096])
Pair 2.170 2.365 0.0022399 [ratio: 5.790 30.320] -0.446 ] llama-3-cat-8b-instruct-pytorch-23 :: Buzz-8b-Large-v0.5-0
Pair 2.170 2.338 0.0801546 [ratio: 16.902 5.358] 1.310 ] Llama-3SOME-8B-v1-18 :: MAmmoTH2-8B-Plus-4
Pair 2.170 2.236 0.3141651 [ratio: 3.581 3.993] -3.427 ] dolphin-2.9-llama3-8b-8 :: Llama-3-Refueled-15
Pair 2.170 2.170 0.6099472 [ratio: 2.442 2.339] -1.231 ] Configurable-Hermes-2-Pro-Llama-3-8B-1 :: Llama-3-LewdPlay-8B-evo-13
Pair 2.170 2.165 0.6262314 [ratio: 2.323 2.445] -1.602 ] opus-v1.2-llama-3-8b-instruct-run3.5-epoch2.5-25 :: Tiamat-8b-1.2-Llama-3-DPO-6
P

In [ ]:
from transformers import AutoModelForCausalLM, AutoTokenizer

out_folder = "./maldv/badger-augment"
in_folder = "./models/delta/base/badger"
tokenizer = AutoTokenizer.from_pretrained(in_folder)
tokenizer.save_pretrained(out_folder)